In [ ]:
## Code for lecture 4: TT-SVD algorithm for a full tensor
import numpy as np

# Create random tensor
d = 10
ndims = np.int_(2*np.ones(d)) # 2 x ... x 2 tensor
X = np.random.rand(*ndims)
X = X/np.linalg.norm(X)
print("Shape", X.shape)
# Alternative: Generate high-order tensor from some function...

# Truncation threshold for TT-SVD method
epsi = 1.0e-1
print("Threshold",epsi)

# Construct TT approximation using TT-SVD
tt_cores = []
ranks = np.int_(np.ones(d+1))
# first reshape into n1 x (n2...nd)
H = X.reshape(ndims[0],np.prod(ndims[1:]))
for mu in range(0,d-1):
    
    # Compute SVD of matricization
    u,s,v = np.linalg.svd(H,full_matrices=False)
    
    # find truncation rank based on threshold
    k = max(np.searchsorted(-s,-epsi),1)
    
    # Store u[:,:k] as TT core
    tt_cores.append(np.reshape(u[:,:k],[ranks[mu],ndims[mu],k]))
    
    # Reshape diag(s)@v into next matrix
    H = np.reshape(v[:k,:]*s[:k,None],([k*ndims[mu+1],np.prod(ndims[mu+2:])]))
    ranks[mu+1] = k
# Store last core
tt_cores.append(np.reshape(H,([k,ndims[d-1],1])))

# Compute some entry by multiplying slices of cores
inds = np.random.randint(np.zeros(d),ndims) #random multi-index
g = tt_cores[0][:,inds[0],:]
for ii in range(1,d):
    g = g@tt_cores[ii][:,inds[ii],:]

# compare with exact value
print("TT ranks",ranks)
print(np.abs(X[*inds] - g[0][0]))
